In [1]:
#import the essential packages
#base packages
import numpy as np
import pandas as pd
import geopandas as gpd

# Plotting packages
import seaborn as sns
from matplotlib import pyplot as plt
import holoviews as hv
import hvplot.pandas

# We use a PySAL example shapefile
import libpysal as ps
import pyogrio

np.random.seed(42)

pd.options.display.max_columns = 999

In [2]:
Raw_data = gpd.read_file("C:\\Users\\zhaiy\\Desktop\\6950\\Final_Project\\output_data\\final_output_data2.shp", engine="pyogrio")
Raw_data.head()

Yunnan_Gen  ZonalSt_Yu ZonalSt__1  ZonalSt__2    ZonalSt__3   ZonalSt__4  \
0       Z-49           1       Z-49           1  10000.000000   842.422414   
1      AA-49           2      AA-49           2   9947.914938  1015.240124   
2      AB-49           3      AB-49           3   9994.723120  1021.375919   
3      AC-49           4      AC-49           4   9901.515000  1189.501402   
4      AD-49           5      AD-49           5   9767.894705  1001.717657   

   sum_Length  In_City  In_Habitat  Shape_Leng  Shape_Area  \
0    0.000000        0           0    0.577634     0.02408   
1    7.992817        0           0    0.577634     0.02408   
2   29.311069        0           1    0.577634     0.02408   
3    5.737393        0           0    0.577634     0.02408   
4   62.130767        0           0    0.577634     0.02408   

                                            geometry  
0  POLYGON ((101.23377 21.22569, 101.18563 21.142...  
1  POLYGON ((101.37817 21.14231, 101.33004 21.058...  
2  POLYGON ((101.52258 21.22569, 101.47445 21.142...  
3  POLYGON ((101.66699 21.14231, 101.61886 21.058...  
4  POLYGON ((101.81140 21.22569, 101.76326 21.142...

In [3]:
Clean_data = Raw_data.drop(["Shape_Leng",'Shape_Area',"Yunnan_Gen","ZonalSt_Yu","ZonalSt__1","ZonalSt__2"],axis=1)
Clean_data = Clean_data.rename(columns={"ZonalSt__3":"forest_source","ZonalSt__4":"avg_altitude","sum_Length":"river_length"})
Clean_data['id'] = range(len(Clean_data))
Clean_data = Clean_data.set_geometry('geometry')
Clean_data

forest_source  avg_altitude  river_length  In_City  In_Habitat  \
0      10000.000000    842.422414      0.000000        0           0   
1       9947.914938   1015.240124      7.992817        0           0   
2       9994.723120   1021.375919     29.311069        0           1   
3       9901.515000   1189.501402      5.737393        0           0   
4       9767.894705   1001.717657     62.130767        0           0   
...             ...           ...           ...      ...         ...   
1609    4082.800000   4939.036814      0.000000        0           0   
1610    7769.413807   3786.816872     32.849415        0           0   
1611    7923.825332   3242.113181     13.113507        0           0   
1612    8869.100600   3912.647315     10.075061        0           0   
1613    7015.519337   3006.693245      2.534275        0           0   

                                               geometry    id  
0     POLYGON ((101.23377 21.22569, 101.18563 21.142...     0  
1     POLYGON ((101.37817 21.14231, 101.33004 21.058...     1  
2     POLYGON ((101.52258 21.22569, 101.47445 21.142...     2  
3     POLYGON ((101.66699 21.14231, 101.61886 21.058...     3  
4     POLYGON ((101.81140 21.22569, 101.76326 21.142...     4  
...                                                 ...   ...  
1609  POLYGON ((98.92323 29.06288, 98.87509 28.97950...  1609  
1610  POLYGON ((99.06764 28.97950, 99.01950 28.89613...  1610  
1611  POLYGON ((99.21205 29.06288, 99.16391 28.97950...  1611  
1612  POLYGON ((99.06764 29.14625, 99.01950 29.06288...  1612  
1613  POLYGON ((99.21205 29.22962, 99.16391 29.14625...  1613  

[1614 rows x 7 columns]

In [21]:
data_tocsv = Clean_data.set_crs("EPSG:4326", inplace=False)
data_tocsv['geometry'] = data_tocsv['geometry'].apply(lambda x: x.wkt)
data_tocsv.to_csv("basic_data2.csv", index=False)

C:\Users\zhaiy\AppData\Local\Temp\ipykernel_23972\3719943487.py:2: UserWarning: Geometry column does not contain geometry.
  data_tocsv['geometry'] = data_tocsv['geometry'].apply(lambda x: x.wkt)


In [4]:
m = Clean_data.set_crs("EPSG:4326", inplace=False).explore('In_Habitat')
m

now, let's convert our polygon data to point data, 

In [5]:
data_projected = Clean_data.to_crs(3857)

# Create a new GeoDataFrame with attributes and central points
point_data = data_projected.assign(centroid=data_projected['geometry'].centroid)

# Calculate centroids
centroids = data_projected['geometry'].centroid

# Create a new GeoDataFrame for centroids
point_data['geometry'] = centroids

point_data.explore("river_length")

In [6]:
from shapely.geometry import Point
point_data.geometry.iloc[0].distance(point_data.geometry.iloc[8])

19924.581230591983

In [11]:
import geopandas as gpd
import networkx as nx
import numpy as np

# 加载 GeoDataFrame
gdf = point_data# 你的 GeoDataFrame 加载方法

# 转换坐标为投影坐标系，以米为单位计算距离
gdf = gdf.to_crs(epsg=3395)  # 使用适合的投影

# 设置权重因子
alpha = 1.0  # 路径长度的影响
beta = 2.0   # forest_source 的影响
gamma = 1.0  # river_length 的影响
delta = 3.0  # avg_altitude 的影响

#set start point, end point
start_id = 30# 起点 ID
end_id = 600# 终点 ID

# get the geometry from start to end
start_point = gdf.loc[gdf['id'] == start_id, 'geometry'].values[0]
end_point = gdf.loc[gdf['id'] == end_id, 'geometry'].values[0]

# caculate the distance of two points
line_distance = start_point.distance(end_point)

# search radius = 1.1* distance
search_radius = line_distance * 1.10

# filter the points within radius
mask = gdf['geometry'].apply(lambda x: x.distance(start_point) <= search_radius or x.distance(end_point) <= search_radius)
pruned_gdf = gdf[mask]

# 创建图
G = nx.Graph()

# 添加节点和边
for i, row_i in pruned_gdf.iterrows():
    for j, row_j in pruned_gdf.iterrows():
        if i != j:
            distance = row_i['geometry'].distance(row_j['geometry'])
            if distance <= 20000:
                edge_weight = (alpha * distance
                               - beta * ((row_i['forest_source'] + row_j['forest_source']) / 2)
                               - gamma * ((row_i['river_length'] + row_j['river_length']) / 2)
                               + delta * ((row_i['avg_altitude'] + row_j['avg_altitude']) / 2))
                G.add_edge(row_i['id'], row_j['id'], weight=edge_weight)

# 计算最短路径
path = nx.shortest_path(G, source=start_id, target=end_id, weight='weight')

# 打印路径上的点的 ID
print("Path IDs:", path)


Path IDs: [30, 31, 46, 47, 65, 83, 100, 101, 122, 149, 185, 186, 225, 226, 268, 269, 316, 317, 368, 369, 421, 422, 477, 478, 538, 539, 600]


In [12]:
# 假设已经计算得到路径 path
# path 是节点ID的列表，如 [1, 5, 10, 20]

# 添加新列，初始化为 'none'
Clean_data['status3'] = 'none'

# 更新起点、终点和途中点的状态
Clean_data.loc[Clean_data['id'] == path[0], 'status3'] = 'start'
Clean_data.loc[Clean_data['id'] == path[-1], 'status3'] = 'end'
Clean_data.loc[Clean_data['id'].isin(path[1:-1]), 'status3'] = 'via'


import folium

# 创建地图对象，初始位置设为第一个点的位置
m = Clean_data.explore('status3')
m

In [16]:
# 假设已经计算得到路径 path
# path 是节点ID的列表，如 [1, 5, 10, 20]

# 添加新列，初始化为 'none'
Clean_data['status'] = 'none'

# 更新起点、终点和途中点的状态
Clean_data.loc[Clean_data['id'] == path[0], 'status'] = 'start'
Clean_data.loc[Clean_data['id'] == path[-1], 'status'] = 'end'
Clean_data.loc[Clean_data['id'].isin(path[1:-1]), 'status'] = 'via'


import folium

# 创建地图对象，初始位置设为第一个点的位置
m = Clean_data.explore('status')
m

In [13]:
result_tocsv = Clean_data.set_crs("EPSG:4326", inplace=False)
result_tocsv['geometry'] = result_tocsv['geometry'].apply(lambda x: x.wkt)
result_tocsv.to_csv("result_data.csv", index=False)

C:\Users\zhaiy\AppData\Local\Temp\ipykernel_49680\4199872578.py:2: UserWarning: Geometry column does not contain geometry.
  result_tocsv['geometry'] = result_tocsv['geometry'].apply(lambda x: x.wkt)


In [14]:
result_tocsv

forest_source  avg_altitude  river_length  In_City  In_Habitat  \
0      10000.000000    842.422414      0.000000        0           0   
1       9947.914938   1015.240124      7.992817        0           0   
2       9994.723120   1021.375919     29.311069        0           1   
3       9901.515000   1189.501402      5.737393        0           0   
4       9767.894705   1001.717657     62.130767        0           0   
...             ...           ...           ...      ...         ...   
1609    4082.800000   4939.036814      0.000000        0           0   
1610    7769.413807   3786.816872     32.849415        0           0   
1611    7923.825332   3242.113181     13.113507        0           0   
1612    8869.100600   3912.647315     10.075061        0           0   
1613    7015.519337   3006.693245      2.534275        0           0   

                                               geometry    id status1 status2  \
0     POLYGON ((101.23376615474899 21.22568672453764...     0    none    none   
1     POLYGON ((101.37817477285603 21.14231237000018...     1    none    none   
2     POLYGON ((101.52258339096329 21.22568672453764...     2    none    none   
3     POLYGON ((101.66699200907033 21.14231237000018...     3    none    none   
4     POLYGON ((101.81140062717736 21.22568672453764...     4    none    none   
...                                                 ...   ...     ...     ...   
1609  POLYGON ((98.9232282650355 29.06287605105655, ...  1609    none    none   
1610  POLYGON ((99.06763688314254 28.979501696519037...  1610    none    none   
1611  POLYGON ((99.21204550124958 29.06287605105655,...  1611    none    none   
1612  POLYGON ((99.06763688314254 29.146250405594003...  1612    none    none   
1613  POLYGON ((99.21204550124958 29.229624760131458...  1613    none    none   

     status3  
0       none  
1       none  
2       none  
3       none  
4       none  
...      ...  
1609    none  
1610    none  
1611    none  
1612    none  
1613    none  

[1614 rows x 10 columns]